In [14]:
import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as animation
from scipy.stats import semicircular
from IPython.display import HTML
import matplotlib
matplotlib.use("TkAgg")

mystyle = "https://raw.githubusercontent.com/quantgirluk/matplotlib-stylesheets/main/quant-pastel-light.mplstyle"
plt.style.use(mystyle)
plt.rcParams["figure.figsize"] = (10,5)


class RandomMatrixGOE:

    def __init__(self, n, random_state: int = None,):
        self.n = n
        self.random_state = random_state
        self.matrix = self.sample()
        self._eigenvalues = None

    def sample(self, random_state: int = None):
        if random_state is not None:
            np.random.seed(random_state)
        matrix = np.random.randn(self.n, self.n)
        self.matrix = (matrix + matrix.transpose()) / np.sqrt(2 * self.n)
        self._eigenvalues = None
        return self.matrix

    def eigenvalues(self) -> np.ndarray:
        if self._eigenvalues:
            return self._eigenvalues
        self._eigenvalues = np.linalg.eigvalsh(self.matrix)
        return self._eigenvalues



HIST_BINS = np.linspace(-2, 2, 40)
matrix0 = RandomMatrixGOE(n=100, random_state=123)
data = matrix0.eigenvalues()

n, _ = np.histogram(data, HIST_BINS, density=True)

def prepare_animation(bar_container):
    def animate(frame_number):
        ax.set_title("Convergence to the Wigner Semicircle Law \n n={}".format(frame_number))
        matrix = RandomMatrixGOE(n=frame_number)
        data = matrix.eigenvalues()
        n, _ = np.histogram(data, HIST_BINS, density=True)

        for count, rect in zip(n, bar_container.patches):
            rect.set_height(count)
        return bar_container.patches
    return animate


fig, ax = plt.subplots()
_, _, bar_container = ax.hist(data, HIST_BINS, lw=1, ec="white", fc="hotpink", alpha=0.5)
rv = semicircular(scale=2)
x = np.linspace(-2.0, 2.0, 1000)
ax.plot(x, rv.pdf(x), label="Probability Density Function", color="dodgerblue")
ax.set_ylim(top=0.45)  # set safe limit to ensure that all data is visible.

frames = np.arange(50, 2001, 50)
ani = animation.FuncAnimation(fig, prepare_animation(bar_container), frames, repeat=False, blit=False, interval=200)


# To save the animation using Pillow as a gif
# writer = animation.PillowWriter(fps=3,
#                                 metadata=dict(artist='@Quant_Girl'),
#                                 bitrate=1800)
# ani.save('18_WignerSemicircle.gif', writer=writer)

HTML(ani.to_jshtml())
